Load necessary prerequisites

In [3]:
pip install ffmpeg-python

Video Processing Functions

In [4]:
import ffmpeg
import os
import csv
import subprocess
import re

def extract_frames(video_path, output_dir, data_folder, csv_path): # modify to extract even unannotated frames, and just have the annotations be whatever the first one is thats in the file until it is touched?
    """
    Extract frames (specified in csv file) from a video using ffmpeg-python.

    :param video_path: Path to the input video file.
    :param output_folder: Path to the output folder where frames will be saved.
    :param data_folder: Name of the folder where the original video data is stored.
    :param csv_path: Path to the input csv file which establishes which frames are to be extracted.
    """
    # Ensure the output directory exists
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)

    # Read the frame numbers from the CSV file
    frame_numbers = []
    with open(csv_path, newline='') as csvfile:
        reader = csv.reader(csvfile)
        next(reader) #skip the header row
        for row in reader:
            frame_numbers.append(int(float(row[0])))

    # Get the base name of the video file (without directory, extension and date tag)
    video_basename = os.path.splitext(os.path.basename(video_path))[0]
    video_basename_no_date = (re.split(r'(_\d{4}-\d{2}-\d{2})', video_basename))[0]

    # Iterate through the frame numbers and extract each frame
    for frame_number in frame_numbers:
        output_file = os.path.join(output_dir, f"{data_folder}_{video_basename_no_date}_frame_{frame_number:03d}.png")
        # Extract the frame using ffmpeg
        command = [
            'ffmpeg',
            '-i', video_path,           # Input file
            '-vf', f'select=eq(n\\,{frame_number})',  # Select specific frame
            '-vsync', 'vfr',            # Variable frame rate
            '-q:v', '2',                # Quality setting for PNG
            '-frames:v', '1',           # Extract only one frame
            output_file
        ]
        try:
            result = subprocess.run(command, check=True, capture_output=True, text=True)
        except subprocess.CalledProcessError as e:
            print(f"Error extracting frame {frame_number}: {e.stderr}")
            raise

def list_avi_files(folder_path):
    """
    Lists all .avi files in the given folder.

    :param folder_path: Path to the folder
    :return: List of .mp4 file names
    """
    try:
        # List all files in the folder
        files = os.listdir(folder_path)
        # Filter out only .avi files
        avi_files = [file for file in files if file.endswith('.avi')]
        return avi_files
    except Exception as e:
        return str(e)


Function to convert single video .csv files into single-frame .txt files

In [5]:
import csv
import os

# Function to read the input CSV file and write each row to its own .txt file
def split_csv_to_txt(input_file_path, output_txt_folder_path, data_folder, current_fish):
    # Ensure the output directory exists
    os.makedirs(output_txt_folder_path, exist_ok=True)

    with open(input_file_path, mode='r', newline='', encoding='utf-8') as infile:
        reader = csv.reader(infile)
        next(reader)  # Skip the header row

        for i, row in enumerate(reader, start=1):
            output_file = os.path.join(output_txt_folder_path, f'{data_folder}_{current_fish}_frame_{int(float(row[0])):03}.txt')
            new_row = ["0", str((float(row[1]))/640), str((float(row[2]))/480), str(28/640), str(28/480)] #creating proper format for frame annotation .txt file
            with open(output_file, mode='w', encoding='utf-8') as outfile:
                outfile.write(' '.join(new_row) + '\n')
            print(f'Written {output_file}')


#Call the function to split the CSV
#split_csv_to_txt("drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response Virginie Pt 2/Old WT 01.csv", "drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response Virginie Pt 2/Old WT 01", "WT Touch Response Virginie Pt 2", "Old WT 01")

Script that extracts frames and annotations from a folder containing one excel file and a bunch of videos

In [29]:
import openpyxl
import csv
import os

def search_files_with_prefix(directory, prefix):
    files = os.listdir(directory)
    matching_files = [f for f in files if f.startswith(prefix)]
    return matching_files

def extract_filename(input_string):
    if '/' in input_string:
        # Split the path using os.path.split and return only the filename
        _, filename = os.path.split(input_string)
        return filename
    else:
        # If no forward slash is found, return the input string as is
        return input_string

def extract_annotations_and_frames(data_folder: str, naming_convention='', leading_zeros=0, col_spacing=9, frame_col_spacing=1, x_col_spacing=3, y_col_spacing=4):
    '''
    Arguments:
      data_folder (str): the name of the folder where the data (.xlsx file and associated videos) are stored
      naming_convention (str): optional arg that details the naming convention that should be used to create the resulting .txt files. It is also necessary
                                for using search_files_with_prefix, in order to extract frames from the corresponding video. If not provided on input, naming_convention is
                                determined by the sheet name, as given by wb.sheetnames.
      leading zeros (int): optional arg that specifies the number of leading zeros for the fish number. If not specified, the default is 0.
      col_spacing (int): optional arg that specifies the total number of columns occupied by a single fish's data in the .xlsx file.
      frame_col_spacing (int): optional arg that specifies the number of the column (assuming each fish's data starts at a 0th column) that contains the frame number data.
      x_col_spacing (int): " " that contains the x coordinate data.
      y_col_spacing (int): " " that contains the y coordinate data.
    Details:
      This is the high-level function where we orchestrate all the steps necessary for obtaining annotations and frames.
      Assumptions:
      1. a folder contains exactly one XLSX file and multiple video files;
      2. the XLSX file has the exact same name as the folder it is in, but with a .xlsx suffix
      Steps:
      0. Create the YAML file with a single class 0: zebrafish, used for the entire dataset
      1. The XLSX file is used as the master file to drive the process. It has the annotations for all
        videos in this folder.
      2. Open and process the XLSX file
      3. foreach ( annotation set in XLSX file ): (because there are multiple videos in the folder)
          1. get the fish number
          2. recreate the prefix of the AVI filename by using the supplied prefix, and appending the fish_id
            with the required number of leading zeros to the end of the prefix
          3. Search the folder for a match using wildcards - we should find exactly one matching file
          4. Create the YOLO-comptabile dataset for this folder:
              0. create and apply the file naming convention for the files (similar or same for images and annotation text files)
              1. extract all needed frames from the video you just found
              2. create the pytorch & YOLO-compatible annotations for every video frame, one file per frame
              3. save the files to the destination folder (and whatever hard-coded subfolders thereunder as required)
    '''
    # Load the workbook
    xlsx_file = data_folder + '.xlsx'
    wb = openpyxl.load_workbook(f'drive/MyDrive/Colab Notebooks/Zebrafish Data/{data_folder}/{xlsx_file}', data_only=True)

    # Ensure output directories exist
    output_dir = f'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/{data_folder}'
    os.makedirs(output_dir, exist_ok=True)

    output_dir_annotations = f'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/{data_folder}/Annotations'
    os.makedirs(output_dir_annotations, exist_ok=True)

    output_dir_frames = f'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/{data_folder}/Frames'
    os.makedirs(output_dir_frames, exist_ok=True)

    # Track fish number for naming csv files
    fish_number = 1

    for sheet in wb.sheetnames:
        ws = wb[sheet]

        # Assuming fish data starts at column 1
        col_start = 1

        while col_start <= ws.max_column:
            # Columns for Frame Number, X, and Y coordinates
            frame_col = col_start + frame_col_spacing
            x_col = col_start + x_col_spacing
            y_col = col_start + y_col_spacing

            # Check if the X column is within the sheet's max column range
            if x_col > ws.max_column:
                break

            # Collect data from the X and Y columns
            frame_data = []
            x_data = []
            y_data = []

            for row in ws.iter_rows(min_row=1, max_row=ws.max_row, min_col=frame_col, max_col=y_col):
                frame_cell = row[0]
                x_cell = row[1]
                y_cell = row[2]
                if frame_cell.value is not None and x_cell.value is not None and y_cell.value is not None:
                    frame_data.append(frame_cell.value)
                    x_data.append(x_cell.value)
                    y_data.append(y_cell.value)

            # Write to a CSV file if we have data
            if frame_data and x_data and y_data:

                #Account for leading zeros in filename, if present
                zeros = ''
                if (leading_zeros != 0) and fish_number < (10*leading_zeros):
                  i=0
                  while i < leading_zeros:
                    zeros += '0'
                    i += 1

                #Define the naming convention based on current sheet, if naming_convention not specified in func input
                if not naming_convention:
                  naming_convention = sheet

                print(naming_convention)
                # Define the CSV file name
                csv_filename = f'{naming_convention}{zeros}{fish_number}.csv'
                csv_path = os.path.join(output_dir, csv_filename)

                # Create the CSV file
                with open(csv_path, 'w', newline='') as csvfile:
                    csvwriter = csv.writer(csvfile)
                    csvwriter.writerow(['Frame Number', 'X', 'Y'])

                    #Write an extra 15 frames into the CSV, these 15 frames precede the first frame where fish moves
                    for i in range(0,15):
                      try:
                        frame_number = (frame_data[0] - (15-i))
                      except Exception as e:
                        print(f"An error occurred in creating {csv_filename}: {e}")
                      if frame_number > 0:
                        csvwriter.writerow([str(frame_number), str(x_data[0]), str(y_data[0])])

                    csvwriter.writerows(zip(frame_data, x_data, y_data))

                print(f'Saved {csv_path}')

                #Find current_fish name for file search purposes
                current_fish = os.path.splitext(csv_filename)[0]

                # Use folder_name to search the video folder directory for a video with a matching name
                video_name = current_fish + '_'
                video_file = search_files_with_prefix(f'drive/MyDrive/Colab Notebooks/Zebrafish Data/{data_folder}', video_name)
                if video_file:
                  print(video_file)
                else:
                  print("Extraction Process Terminated. Reason: No Video Found")
                  return

                # Extract the individual frame .txt files from the video CSV file
                split_csv_to_txt(csv_path, output_dir_annotations, data_folder, current_fish)

                # Extract only the relevant frames from the video file
                extract_frames(f'drive/MyDrive/Colab Notebooks/Zebrafish Data/{data_folder}/{video_file[0]}', output_dir_frames, data_folder, csv_path)

            # Move to the next fish data block
            col_start += col_spacing
            fish_number += 1
            #break #for testing




Make sure Drive is properly refreshed before initiating extraction (restart runtime or run drive.mount())

In [51]:
from google.colab import drive

drive.mount("/content/drive", force_remount=True)

Mounted at /content/drive


In [39]:
!ls "drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations"

'+ + (11 06 2021)'			   'R536H R536H (11 06 2021)'
'- - 14 10 2022'			   'R536H R536H (17 04 2021)'
'+ + (15 07 2021)'			   'R536H R536H (28 05 2021)'
'+ + (17 04 2021)'			   'TDP43 G348C Touch Response 31-07-24'
'- - 20 03 2022'			   'Tyler Double KO Touch Responses'
'+ + (28 05 2021)'			   'Tyler STMN2a Touch Responses'
'CRISPent inppf5 Touch Response 12-06-24'  'Tyler STMN2b Touch Responses'
'R526H + (05 08 2021)'			   'WT Touch Response 06-06-24'
'R536H + (03 06 2021)'			   'WT Touch Response 30-05-24'
'R536H+ (08 07 2021)'			   'WT Touch Response Virginie Pt 2'
'R536H + (20 05 2021)'			    zebratrack.yaml
'R536H R536H (05 08 2021)'


Run the extract_annotations_and_frames function to extract frams and annotations for all data.

In [ ]:
#Virginie Dataset
#extract_annotations_and_frames('WT Touch Response Virginie Pt 2', 'Old WT ', 1, 10)


Old WT 
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response Virginie Pt 2/Old WT 01.csv
['Old WT 01_2023-07-13-131916-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response Virginie Pt 2/Annotations/WT Touch Response Virginie Pt 2_Old WT 01_frame_004.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response Virginie Pt 2/Annotations/WT Touch Response Virginie Pt 2_Old WT 01_frame_005.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response Virginie Pt 2/Annotations/WT Touch Response Virginie Pt 2_Old WT 01_frame_006.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response Virginie Pt 2/Annotations/WT Touch Response Virginie Pt 2_Old WT 01_frame_007.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response Virginie Pt 2/Annotations/WT Touch Response Virginie Pt 2_Old W

TypeError: unsupported operand type(s) for -: 'str' and 'int'

In [ ]:
#My WT Dataset from May 30th 2024
#extract_annotations_and_frames('WT Touch Response 30-05-24', col_spacing=12)


TR_WT_53hpf_
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response 30-05-24/TR_WT_53hpf_1.csv
['TR_WT_53hpf_1_2024-05-30-144251-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response 30-05-24/Annotations/WT Touch Response 30-05-24_TR_WT_53hpf_1_frame_027.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response 30-05-24/Annotations/WT Touch Response 30-05-24_TR_WT_53hpf_1_frame_028.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response 30-05-24/Annotations/WT Touch Response 30-05-24_TR_WT_53hpf_1_frame_029.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response 30-05-24/Annotations/WT Touch Response 30-05-24_TR_WT_53hpf_1_frame_030.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response 30-05-24/Annotations/WT Touch Response 30-05-24_TR_WT_53hpf_1_frame_031.txt
Wri

In [ ]:
#My WT Dataset from June 6th 2024
#extract_annotations_and_frames('WT Touch Response 06-06-24', col_spacing=10)

#N.B. IGNORE ERROR! Function executed properly, just a formatting difference in this file results in an error being raised instead of the function returning normally

TR_WT_52hpf_
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response 06-06-24/TR_WT_52hpf_1.csv
['TR_WT_52hpf_1_2024-06-06-131215-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response 06-06-24/Annotations/WT Touch Response 06-06-24_TR_WT_52hpf_1_frame_026.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response 06-06-24/Annotations/WT Touch Response 06-06-24_TR_WT_52hpf_1_frame_027.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response 06-06-24/Annotations/WT Touch Response 06-06-24_TR_WT_52hpf_1_frame_028.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response 06-06-24/Annotations/WT Touch Response 06-06-24_TR_WT_52hpf_1_frame_029.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/WT Touch Response 06-06-24/Annotations/WT Touch Response 06-06-24_TR_WT_52hpf_1_frame_030.txt
Wri

In [ ]:
#My inppf5/WT Dataset from June 12th 2024
#extract_annotations_and_frames('CRISPent inppf5 Touch Response 12-06-24', col_spacing=10)


TR_inppf5_52hpf_
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPent inppf5 Touch Response 12-06-24/TR_inppf5_52hpf_1.csv
['TR_inppf5_52hpf_1_2024-06-12-123203-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPent inppf5 Touch Response 12-06-24/Annotations/CRISPent inppf5 Touch Response 12-06-24_TR_inppf5_52hpf_1_frame_015.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPent inppf5 Touch Response 12-06-24/Annotations/CRISPent inppf5 Touch Response 12-06-24_TR_inppf5_52hpf_1_frame_016.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPent inppf5 Touch Response 12-06-24/Annotations/CRISPent inppf5 Touch Response 12-06-24_TR_inppf5_52hpf_1_frame_017.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPent inppf5 Touch Response 12-06-24/Annotations/CRISPent inppf5 Touch Response 12-06-24_TR_inppf5_52hpf_1_frame_018.txt
Written drive/MyDrive/C

In [ ]:
#Tyler STMN2a Dataset
#extract_annotations_and_frames('Tyler STMN2a Touch Responses', col_spacing=7)


2a KO 
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler STMN2a Touch Responses/2a KO 1.csv
['2a KO 1_2023-11-23-124915-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler STMN2a Touch Responses/Annotations/Tyler STMN2a Touch Responses_2a KO 1_frame_051.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler STMN2a Touch Responses/Annotations/Tyler STMN2a Touch Responses_2a KO 1_frame_052.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler STMN2a Touch Responses/Annotations/Tyler STMN2a Touch Responses_2a KO 1_frame_053.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler STMN2a Touch Responses/Annotations/Tyler STMN2a Touch Responses_2a KO 1_frame_054.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler STMN2a Touch Responses/Annotations/Tyler STMN2a Touch Responses_2a KO 1_frame_055.txt
Written drive/MyDrive/Colab N

In [ ]:
#Tyler STMN2b Dataset
#extract_annotations_and_frames('Tyler STMN2b Touch Responses', col_spacing=7)


2b KO 
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler STMN2b Touch Responses/2b KO 1.csv
['2b KO 1_2023-09-01-143500-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler STMN2b Touch Responses/Annotations/Tyler STMN2b Touch Responses_2b KO 1_frame_050.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler STMN2b Touch Responses/Annotations/Tyler STMN2b Touch Responses_2b KO 1_frame_051.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler STMN2b Touch Responses/Annotations/Tyler STMN2b Touch Responses_2b KO 1_frame_052.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler STMN2b Touch Responses/Annotations/Tyler STMN2b Touch Responses_2b KO 1_frame_053.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler STMN2b Touch Responses/Annotations/Tyler STMN2b Touch Responses_2b KO 1_frame_054.txt
Written drive/MyDrive/Colab N

In [ ]:
#Tyler Double KO Dataset
#extract_annotations_and_frames('Tyler Double KO Touch Responses', col_spacing=9,  y_col_spacing=5)

Double KO 
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler Double KO Touch Responses/Double KO 1.csv
['Double KO 1_2023-11-02-102254-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler Double KO Touch Responses/Annotations/Tyler Double KO Touch Responses_Double KO 1_frame_047.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler Double KO Touch Responses/Annotations/Tyler Double KO Touch Responses_Double KO 1_frame_048.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler Double KO Touch Responses/Annotations/Tyler Double KO Touch Responses_Double KO 1_frame_049.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler Double KO Touch Responses/Annotations/Tyler Double KO Touch Responses_Double KO 1_frame_050.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/Tyler Double KO Touch Responses/Annotations/Tyler Double KO Touch 

For Dataset V3: Extract Christian's data and my new data

In [18]:
# Christian -- 14 10 2022
extract_annotations_and_frames(data_folder='- - 14 10 2022', naming_convention='#', col_spacing=11, frame_col_spacing=0, x_col_spacing=2, y_col_spacing=3)

#
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 14 10 2022/#1.csv
['#1_2021-10-14-131743-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 14 10 2022/Annotations/- - 14 10 2022_#1_frame_175.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 14 10 2022/Annotations/- - 14 10 2022_#1_frame_176.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 14 10 2022/Annotations/- - 14 10 2022_#1_frame_177.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 14 10 2022/Annotations/- - 14 10 2022_#1_frame_178.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 14 10 2022/Annotations/- - 14 10 2022_#1_frame_179.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 14 10 2022/Annotations/- - 14 10 2022_#1_frame_180.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 14 10 2022/Annotat

In [19]:
# Christian -- 20 03 2022
extract_annotations_and_frames(data_folder='- - 20 03 2022', naming_convention='#', col_spacing=11, frame_col_spacing=0, x_col_spacing=2, y_col_spacing=3)

#
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 20 03 2022/#1.csv
['#1_2022-03-20-131453-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 20 03 2022/Annotations/- - 20 03 2022_#1_frame_105.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 20 03 2022/Annotations/- - 20 03 2022_#1_frame_106.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 20 03 2022/Annotations/- - 20 03 2022_#1_frame_107.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 20 03 2022/Annotations/- - 20 03 2022_#1_frame_108.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 20 03 2022/Annotations/- - 20 03 2022_#1_frame_109.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 20 03 2022/Annotations/- - 20 03 2022_#1_frame_110.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/- - 20 03 2022/Annotat

In [20]:
# Christian ++ (11 06 2021)
extract_annotations_and_frames(data_folder='+ + (11 06 2021)', naming_convention='#', col_spacing=11, frame_col_spacing=0, x_col_spacing=2, y_col_spacing=3)

#
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (11 06 2021)/#1.csv
['#1_2021-06-11-133054-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (11 06 2021)/Annotations/+ + (11 06 2021)_#1_frame_103.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (11 06 2021)/Annotations/+ + (11 06 2021)_#1_frame_104.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (11 06 2021)/Annotations/+ + (11 06 2021)_#1_frame_105.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (11 06 2021)/Annotations/+ + (11 06 2021)_#1_frame_106.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (11 06 2021)/Annotations/+ + (11 06 2021)_#1_frame_107.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (11 06 2021)/Annotations/+ + (11 06 2021)_#1_frame_108.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotati

In [21]:
# Christian ++ (15 07 2021)
extract_annotations_and_frames(data_folder='+ + (15 07 2021)', naming_convention='#', col_spacing=11, frame_col_spacing=0, x_col_spacing=2, y_col_spacing=3)

#
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (15 07 2021)/#1.csv
['#1_2021-07-15-134806-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (15 07 2021)/Annotations/+ + (15 07 2021)_#1_frame_476.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (15 07 2021)/Annotations/+ + (15 07 2021)_#1_frame_477.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (15 07 2021)/Annotations/+ + (15 07 2021)_#1_frame_478.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (15 07 2021)/Annotations/+ + (15 07 2021)_#1_frame_479.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (15 07 2021)/Annotations/+ + (15 07 2021)_#1_frame_480.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (15 07 2021)/Annotations/+ + (15 07 2021)_#1_frame_481.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotati

In [22]:
# Christian ++ (17 04 2021)
extract_annotations_and_frames(data_folder='+ + (17 04 2021)', naming_convention='#', col_spacing=11, frame_col_spacing=0, x_col_spacing=2, y_col_spacing=3)

#
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (17 04 2021)/#2.csv
['#2_2021-04-17-100713-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (17 04 2021)/Annotations/+ + (17 04 2021)_#2_frame_102.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (17 04 2021)/Annotations/+ + (17 04 2021)_#2_frame_103.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (17 04 2021)/Annotations/+ + (17 04 2021)_#2_frame_104.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (17 04 2021)/Annotations/+ + (17 04 2021)_#2_frame_105.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (17 04 2021)/Annotations/+ + (17 04 2021)_#2_frame_106.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (17 04 2021)/Annotations/+ + (17 04 2021)_#2_frame_107.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotati

In [23]:
# Christian ++ (28 05 2021)
extract_annotations_and_frames(data_folder='+ + (28 05 2021)', naming_convention='#', col_spacing=11, frame_col_spacing=0, x_col_spacing=2, y_col_spacing=3)

#
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (28 05 2021)/#1.csv
['#1_2021-05-28-145113-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (28 05 2021)/Annotations/+ + (28 05 2021)_#1_frame_132.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (28 05 2021)/Annotations/+ + (28 05 2021)_#1_frame_133.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (28 05 2021)/Annotations/+ + (28 05 2021)_#1_frame_134.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (28 05 2021)/Annotations/+ + (28 05 2021)_#1_frame_135.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (28 05 2021)/Annotations/+ + (28 05 2021)_#1_frame_136.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/+ + (28 05 2021)/Annotations/+ + (28 05 2021)_#1_frame_137.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotati

In [26]:
# Christian R526H + (05 08 2021)
extract_annotations_and_frames(data_folder='R526H + (05 08 2021)', naming_convention='#', col_spacing=11, frame_col_spacing=0, x_col_spacing=2, y_col_spacing=3)

#
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R526H + (05 08 2021)/#1.csv
['#1_2021-08-05-132949-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R526H + (05 08 2021)/Annotations/R526H + (05 08 2021)_#1_frame_132.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R526H + (05 08 2021)/Annotations/R526H + (05 08 2021)_#1_frame_133.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R526H + (05 08 2021)/Annotations/R526H + (05 08 2021)_#1_frame_134.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R526H + (05 08 2021)/Annotations/R526H + (05 08 2021)_#1_frame_135.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R526H + (05 08 2021)/Annotations/R526H + (05 08 2021)_#1_frame_136.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R526H + (05 08 2021)/Annotations/R526H + (05 08 2021)_#1_frame_137.txt
Written drive/M

In [27]:
# Christian R536H + (03 06 2021)
extract_annotations_and_frames(data_folder='R536H + (03 06 2021)', naming_convention='#', col_spacing=11, frame_col_spacing=0, x_col_spacing=2, y_col_spacing=3)

#
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H + (03 06 2021)/#1.csv
['#1_2021-06-03-121904-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H + (03 06 2021)/Annotations/R536H + (03 06 2021)_#1_frame_186.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H + (03 06 2021)/Annotations/R536H + (03 06 2021)_#1_frame_187.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H + (03 06 2021)/Annotations/R536H + (03 06 2021)_#1_frame_188.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H + (03 06 2021)/Annotations/R536H + (03 06 2021)_#1_frame_189.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H + (03 06 2021)/Annotations/R536H + (03 06 2021)_#1_frame_190.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H + (03 06 2021)/Annotations/R536H + (03 06 2021)_#1_frame_191.txt
Written drive/M

In [28]:
# Christian R536H + (20 05 2021)
extract_annotations_and_frames(data_folder='R536H + (20 05 2021)', naming_convention='#', col_spacing=11, frame_col_spacing=0, x_col_spacing=2, y_col_spacing=3)

#
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H + (20 05 2021)/#1.csv
['#1_2021-05-20-133001-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H + (20 05 2021)/Annotations/R536H + (20 05 2021)_#1_frame_036.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H + (20 05 2021)/Annotations/R536H + (20 05 2021)_#1_frame_037.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H + (20 05 2021)/Annotations/R536H + (20 05 2021)_#1_frame_038.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H + (20 05 2021)/Annotations/R536H + (20 05 2021)_#1_frame_039.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H + (20 05 2021)/Annotations/R536H + (20 05 2021)_#1_frame_040.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H + (20 05 2021)/Annotations/R536H + (20 05 2021)_#1_frame_041.txt
Written drive/M

In [29]:
# Christian R536H R536H (05 08 2021)
extract_annotations_and_frames(data_folder='R536H R536H (05 08 2021)', naming_convention='#', col_spacing=11, frame_col_spacing=0, x_col_spacing=2, y_col_spacing=3)

#
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (05 08 2021)/#1.csv
['#1_2021-08-05-142334-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (05 08 2021)/Annotations/R536H R536H (05 08 2021)_#1_frame_126.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (05 08 2021)/Annotations/R536H R536H (05 08 2021)_#1_frame_127.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (05 08 2021)/Annotations/R536H R536H (05 08 2021)_#1_frame_128.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (05 08 2021)/Annotations/R536H R536H (05 08 2021)_#1_frame_129.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (05 08 2021)/Annotations/R536H R536H (05 08 2021)_#1_frame_130.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (05 08 2021)/Annotations/R536H

In [30]:
# Christian R536H R536H (11 06 2021)
extract_annotations_and_frames(data_folder='R536H R536H (11 06 2021)', naming_convention='#', col_spacing=11, frame_col_spacing=0, x_col_spacing=2, y_col_spacing=3)

#
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (11 06 2021)/#1.csv
['#1_2021-06-11-152450-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (11 06 2021)/Annotations/R536H R536H (11 06 2021)_#1_frame_138.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (11 06 2021)/Annotations/R536H R536H (11 06 2021)_#1_frame_139.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (11 06 2021)/Annotations/R536H R536H (11 06 2021)_#1_frame_140.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (11 06 2021)/Annotations/R536H R536H (11 06 2021)_#1_frame_141.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (11 06 2021)/Annotations/R536H R536H (11 06 2021)_#1_frame_142.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (11 06 2021)/Annotations/R536H

In [31]:
# Christian R536H R536H (17 05 2021)
extract_annotations_and_frames(data_folder='R536H R536H (17 04 2021)', naming_convention='#', col_spacing=11, frame_col_spacing=0, x_col_spacing=2, y_col_spacing=3)

#
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (17 04 2021)/#16.csv
['#16_2021-04-17-091146-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (17 04 2021)/Annotations/R536H R536H (17 04 2021)_#16_frame_053.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (17 04 2021)/Annotations/R536H R536H (17 04 2021)_#16_frame_054.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (17 04 2021)/Annotations/R536H R536H (17 04 2021)_#16_frame_055.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (17 04 2021)/Annotations/R536H R536H (17 04 2021)_#16_frame_056.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (17 04 2021)/Annotations/R536H R536H (17 04 2021)_#16_frame_057.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (17 04 2021)/Annotation

In [32]:
# Christian R536H R536H (28 05 2021)
extract_annotations_and_frames(data_folder='R536H R536H (28 05 2021)', naming_convention='#', col_spacing=11, frame_col_spacing=0, x_col_spacing=2, y_col_spacing=3)

#
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (28 05 2021)/#1.csv
['#1_2021-05-28-132736-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (28 05 2021)/Annotations/R536H R536H (28 05 2021)_#1_frame_190.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (28 05 2021)/Annotations/R536H R536H (28 05 2021)_#1_frame_191.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (28 05 2021)/Annotations/R536H R536H (28 05 2021)_#1_frame_192.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (28 05 2021)/Annotations/R536H R536H (28 05 2021)_#1_frame_193.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (28 05 2021)/Annotations/R536H R536H (28 05 2021)_#1_frame_194.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H R536H (28 05 2021)/Annotations/R536H

In [33]:
# Christian R536H+ (08 07 2021)
extract_annotations_and_frames(data_folder='R536H+ (08 07 2021)', naming_convention='#', col_spacing=11, frame_col_spacing=0, x_col_spacing=2, y_col_spacing=3)

#
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H+ (08 07 2021)/#1.csv
['#1_2021-07-08-123734-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H+ (08 07 2021)/Annotations/R536H+ (08 07 2021)_#1_frame_095.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H+ (08 07 2021)/Annotations/R536H+ (08 07 2021)_#1_frame_096.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H+ (08 07 2021)/Annotations/R536H+ (08 07 2021)_#1_frame_097.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H+ (08 07 2021)/Annotations/R536H+ (08 07 2021)_#1_frame_098.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H+ (08 07 2021)/Annotations/R536H+ (08 07 2021)_#1_frame_099.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/R536H+ (08 07 2021)/Annotations/R536H+ (08 07 2021)_#1_frame_100.txt
Written drive/MyDrive/Colab 

In [23]:
# Me TDP43 G348C Touch Response 31-07-24
extract_annotations_and_frames(data_folder='TDP43 G348C Touch Response 31-07-24', col_spacing=7, frame_col_spacing=1, x_col_spacing=2, y_col_spacing=3)

TR_WT_54hpf_
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/TDP43 G348C Touch Response 31-07-24/TR_WT_54hpf_1.csv
['TR_WT_54hpf_1_2024-07-31-140329-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/TDP43 G348C Touch Response 31-07-24/Annotations/TDP43 G348C Touch Response 31-07-24_TR_WT_54hpf_1_frame_015.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/TDP43 G348C Touch Response 31-07-24/Annotations/TDP43 G348C Touch Response 31-07-24_TR_WT_54hpf_1_frame_016.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/TDP43 G348C Touch Response 31-07-24/Annotations/TDP43 G348C Touch Response 31-07-24_TR_WT_54hpf_1_frame_017.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/TDP43 G348C Touch Response 31-07-24/Annotations/TDP43 G348C Touch Response 31-07-24_TR_WT_54hpf_1_frame_018.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/TDP43 G348C Touc

In [49]:
# Me TDP43 G348C Touch Response 02-08-24
extract_annotations_and_frames(data_folder='TDP43 G348C Touch Response 02-08-24', col_spacing=9, frame_col_spacing=2, x_col_spacing=3, y_col_spacing=4)

TR_WT_
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/TDP43 G348C Touch Response 02-08-24/TR_WT_1.csv
['TR_WT_1_2024-08-02-125217-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/TDP43 G348C Touch Response 02-08-24/Annotations/TDP43 G348C Touch Response 02-08-24_TR_WT_1_frame_015.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/TDP43 G348C Touch Response 02-08-24/Annotations/TDP43 G348C Touch Response 02-08-24_TR_WT_1_frame_016.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/TDP43 G348C Touch Response 02-08-24/Annotations/TDP43 G348C Touch Response 02-08-24_TR_WT_1_frame_017.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/TDP43 G348C Touch Response 02-08-24/Annotations/TDP43 G348C Touch Response 02-08-24_TR_WT_1_frame_018.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/TDP43 G348C Touch Response 02-08-24/Annotations/TDP43 G348

Re-run this one for the high group

In [52]:
# Me CRISPant inppf5 TDP43 rescue 09-08-24
extract_annotations_and_frames(data_folder='CRISPant inppf5 TDP43 rescue 09-08-24', col_spacing=9, frame_col_spacing=2, x_col_spacing=3, y_col_spacing=4)

TR_TDP43_inppf5high_
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 TDP43 rescue 09-08-24/TR_TDP43_inppf5high_1.csv
['TR_TDP43_inppf5high_1_2024-08-09-123749-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 TDP43 rescue 09-08-24/Annotations/CRISPant inppf5 TDP43 rescue 09-08-24_TR_TDP43_inppf5high_1_frame_018.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 TDP43 rescue 09-08-24/Annotations/CRISPant inppf5 TDP43 rescue 09-08-24_TR_TDP43_inppf5high_1_frame_019.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 TDP43 rescue 09-08-24/Annotations/CRISPant inppf5 TDP43 rescue 09-08-24_TR_TDP43_inppf5high_1_frame_020.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 TDP43 rescue 09-08-24/Annotations/CRISPant inppf5 TDP43 rescue 09-08-24_TR_TDP43_inppf5high_1_frame_021.txt
Written drive

In [50]:
# Me CRISPant inppf5 TDP43 rescue 15-08-24
extract_annotations_and_frames(data_folder='CRISPant inppf5 TDP43 rescue 15-08-24', col_spacing=9, frame_col_spacing=2, x_col_spacing=3, y_col_spacing=4)

TR_WT_
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 TDP43 rescue 15-08-24/TR_WT_1.csv
['TR_WT_1_2024-08-15-131421-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 TDP43 rescue 15-08-24/Annotations/CRISPant inppf5 TDP43 rescue 15-08-24_TR_WT_1_frame_010.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 TDP43 rescue 15-08-24/Annotations/CRISPant inppf5 TDP43 rescue 15-08-24_TR_WT_1_frame_011.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 TDP43 rescue 15-08-24/Annotations/CRISPant inppf5 TDP43 rescue 15-08-24_TR_WT_1_frame_012.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 TDP43 rescue 15-08-24/Annotations/CRISPant inppf5 TDP43 rescue 15-08-24_TR_WT_1_frame_013.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 TDP43 rescue 15-08-24/An

In [47]:
# Me CRISPant inppf5 and mutTDP43 Touch Response 18-08-24
extract_annotations_and_frames(data_folder='CRISPant inppf5 and mutTDP43 Touch Response 18-08-24', col_spacing=9, frame_col_spacing=2, x_col_spacing=3, y_col_spacing=4)

TR_TDP43_
Saved drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 and mutTDP43 Touch Response 18-08-24/TR_TDP43_1.csv
['TR_TDP43_1_2024-08-18-130448-0000.avi']
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 and mutTDP43 Touch Response 18-08-24/Annotations/CRISPant inppf5 and mutTDP43 Touch Response 18-08-24_TR_TDP43_1_frame_016.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 and mutTDP43 Touch Response 18-08-24/Annotations/CRISPant inppf5 and mutTDP43 Touch Response 18-08-24_TR_TDP43_1_frame_017.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 and mutTDP43 Touch Response 18-08-24/Annotations/CRISPant inppf5 and mutTDP43 Touch Response 18-08-24_TR_TDP43_1_frame_018.txt
Written drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/CRISPant inppf5 and mutTDP43 Touch Response 18-08-24/Annotations/CRISPant inppf5 and mutTDP43 Touc

Count the number of frames and annotations to make sure they are the same

In [53]:
import os
from google.colab import drive

drive.mount("/content/drive", force_remount=True)

def count_files_in_directory(directory_path):
    """
    Count the number of files in the given directory.

    Parameters:
    directory_path (str): The path to the directory.

    Returns:
    int: The number of files in the directory.
    """
    try:
        # List all entries in the directory
        entries = os.listdir(directory_path)
        # Count the number of files
        file_count = sum(1 for entry in entries if os.path.isfile(os.path.join(directory_path, entry)))
        return file_count
    except FileNotFoundError:
        print(f"The directory {directory_path} does not exist.")
        return 0
    except Exception as e:
        print(f"An error occurred: {e}")
        return 0

def list_directories_and_count_subdirs(directory):
    try:
        # List all directories in the given directory
        with os.scandir(directory) as entries:
            for entry in entries:
                if entry.is_dir():
                    print(f"----------Sub-Directory: {entry.name}----------")
                    # Call count_files_in_directory on each subdirectory
                    subdir_frames = entry.path + "/Frames"
                    subdir_annotations = entry.path + "/Annotations"
                    print(f'The number of files in {entry.name}/Frames is: {count_files_in_directory(subdir_frames)}')
                    print(f'The number of files in {entry.name}/Annotations is: {count_files_in_directory(subdir_annotations)}')
    except FileNotFoundError:
        print(f"The directory '{directory}' does not exist.")
    except PermissionError:
        print(f"Permission denied to access '{directory}'.")


Mounted at /content/drive


Script that counts all files created by previous extract function

N.B. ONLY runs properly when all subdirectories in "Zebrafish Frames and Annotations" contain the subdirectories "Frames" and "Annotations", i.e. if you have already run the copy_subdirectory_contents_to_master to create "images" and "labels" this code will not work.

In [54]:
 list_directories_and_count_subdirs("drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations")


----------Sub-Directory: WT Touch Response Virginie Pt 2----------
The number of files in WT Touch Response Virginie Pt 2/Frames is: 2034
The number of files in WT Touch Response Virginie Pt 2/Annotations is: 2034
----------Sub-Directory: WT Touch Response 30-05-24----------
The number of files in WT Touch Response 30-05-24/Frames is: 1603
The number of files in WT Touch Response 30-05-24/Annotations is: 1603
----------Sub-Directory: WT Touch Response 06-06-24----------
The number of files in WT Touch Response 06-06-24/Frames is: 1977
The number of files in WT Touch Response 06-06-24/Annotations is: 1977
----------Sub-Directory: CRISPent inppf5 Touch Response 12-06-24----------
The number of files in CRISPent inppf5 Touch Response 12-06-24/Frames is: 3896
The number of files in CRISPent inppf5 Touch Response 12-06-24/Annotations is: 3896
----------Sub-Directory: Tyler STMN2a Touch Responses----------
The number of files in Tyler STMN2a Touch Responses/Frames is: 2229
The number of file

Extract data from each of the data folders into two master Frames/Annotations folders

In [55]:
import os
import shutil

def copy_subdirectory_contents_to_master(master_frames_dir, master_annotations_dir, base_dir):
    # Ensure the master directories exist
    os.makedirs(master_frames_dir, exist_ok=True)
    os.makedirs(master_annotations_dir, exist_ok=True)

    # Walk through the base directory
    for subdir in os.listdir(base_dir):
        subdir_path = os.path.join(base_dir, subdir)

        if os.path.isdir(subdir_path):
            frames_subdir = os.path.join(subdir_path, 'Frames')
            annotations_subdir = os.path.join(subdir_path, 'Annotations')

            # Copy frames if the Frames subdirectory exists
            if os.path.exists(frames_subdir):
                for item in os.listdir(frames_subdir):
                    item_path = os.path.join(frames_subdir, item)
                    if os.path.isfile(item_path):
                        shutil.copy(item_path, master_frames_dir)
                    elif os.path.isdir(item_path):
                        shutil.copytree(item_path, os.path.join(master_frames_dir, item), dirs_exist_ok=True)

            # Copy annotations if the Annotations subdirectory exists
            if os.path.exists(annotations_subdir):
                for item in os.listdir(annotations_subdir):
                    item_path = os.path.join(annotations_subdir, item)
                    if os.path.isfile(item_path):
                        shutil.copy(item_path, master_annotations_dir)
                    elif os.path.isdir(item_path):
                        shutil.copytree(item_path, os.path.join(master_annotations_dir, item), dirs_exist_ok=True)


Using the above function to extract subfolder data into master "images" and "labels" directories

In [56]:
master_frames = 'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/images'
master_annotations = 'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/labels'
base_directory = 'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations'

copy_subdirectory_contents_to_master(master_frames, master_annotations, base_directory)

Using "count_files_in_directories" func to ensure data extraction went smoothly.

N.B. The # of files in "images" and "labels" should be identical

In [62]:
print(f"----------Sub-Directories: images and labels----------")
# Call count_files_in_directory on each subdirectory
subdir_frames = "drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations" + "/images"
subdir_annotations = "drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations" + "/labels"
print(f'The number of files in /images is: {count_files_in_directory(subdir_frames)}')
print(f'The number of files in /labels is: {count_files_in_directory(subdir_annotations)}')

----------Sub-Directories: images and labels----------
The number of files in /images is: 65416
The number of files in /labels is: 65416


Delete any missing files (if any)

In [61]:
import os
import subprocess

def find_celibate_files(txt_directory, png_directory):
    try:
        # List all .txt files in the first directory
        txt_files = [f for f in os.listdir(txt_directory) if f.endswith('.txt')]

        for txt_file in txt_files:
            # Construct the expected .png file name
            png_file = txt_file.replace('.txt', '.png')
            png_path = os.path.join(png_directory, png_file)

            if not os.path.exists(png_path):
                print(f"No match was found for the following .txt file and it will be deleted: {txt_file}")
                filepath = f'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/labels/{txt_file}'
                subprocess.run(['rm', filepath])

    except FileNotFoundError as e:
        print(f"Error: {e}")
    except PermissionError as e:
        print(f"Permission denied: {e}")

# Example usage
find_celibate_files('drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/labels', 'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/images')


No match was found for the following .txt file and it will be deleted: Tyler Double KO Touch Responses_Double KO 15_frame_299.txt
No match was found for the following .txt file and it will be deleted: Tyler Double KO Touch Responses_Double KO 12_frame_298.txt
No match was found for the following .txt file and it will be deleted: TDP43 G348C Touch Response 02-08-24_TR_TDP43high_15_frame_088.txt
No match was found for the following .txt file and it will be deleted: TDP43 G348C Touch Response 02-08-24_TR_TDP43high_15_frame_089.txt
No match was found for the following .txt file and it will be deleted: TDP43 G348C Touch Response 02-08-24_TR_TDP43high_15_frame_090.txt
No match was found for the following .txt file and it will be deleted: TDP43 G348C Touch Response 02-08-24_TR_TDP43high_15_frame_091.txt
No match was found for the following .txt file and it will be deleted: TDP43 G348C Touch Response 02-08-24_TR_TDP43high_15_frame_092.txt
No match was found for the following .txt file and it w

Remove the files found in the previous block by "find_celibate_files"

In [ ]:
!rm 'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/labels/Tyler Double KO Touch Responses_Double KO 15_frame_298.txt'
!rm 'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/labels/Tyler Double KO Touch Responses_Double KO 15_frame_299.txt'

Clear Annotations and Frames Directories (For use during testing only  --- RUN WITH EXTREME CAUTION)

In [ ]:
import os
import glob


def empty_two_directories(dir1, dir2):
  confirmation = input("Please Confirm (Type 'Y'): ")

  if confirmation == "Y":
    files = glob.glob(f'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/{dir1}')
    for f in files:
        os.remove(f)

    files = glob.glob(f'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/{dir2}')
    for f in files:
        os.remove(f)
    print("Directories cleared")
  else:
    print("Cancelled")

#empty_two_directories('Tyler STMN2b Touch Responses/Annotations/Tyler STMN2b Touch Responses_2b KO *',
                      #'Tyler STMN2b Touch Responses/Frames/Tyler STMN2b Touch Responses_2b KO *')

Please Confirm (Type 'Y'): Y
Directories cleared


Code for double checking that an annotation makes sense for a given .txt/.png pair

In [ ]:
import os
import random
import cv2  # OpenCV for image processing

def overlay_bounding_box(labels_dir, images_dir, output_dir):
    # Ensure the output directory exists
    os.makedirs(output_dir, exist_ok=True)

    # Get a list of all .txt files in the labels directory
    txt_files = [f for f in os.listdir(labels_dir) if f.endswith('.txt')]

    # If there are no .txt files, return None
    if not txt_files:
        print("No .txt files found in the labels directory.")
        return None

    # Select a random .txt file
    selected_txt_file = random.choice(txt_files)

    # Derive the corresponding .png file name
    base_name = os.path.splitext(selected_txt_file)[0]
    corresponding_png_file = base_name + '.png'

    # Check if the corresponding .png file exists in the images directory
    if corresponding_png_file not in os.listdir(images_dir):
        print(f"Corresponding .png file not found for {selected_txt_file}.")
        return None

    # Read the contents of the selected .txt file
    with open(os.path.join(labels_dir, selected_txt_file), 'r') as file:
        line = file.readline().strip()

    # Parse the line into a list of values
    values = line.split()

    # Ensure the line contains exactly 5 columns
    if len(values) != 5:
        print(f"Unexpected format in {selected_txt_file}. Expected 5 columns, got {len(values)}.")
        return None

    # Extract the required values
    label = int(values[0])
    x_center = float(values[1])
    y_center = float(values[2])
    x_len = float(values[3])
    y_height = float(values[4])

    # Load the corresponding image
    image_path = os.path.join(images_dir, corresponding_png_file)
    image = cv2.imread(image_path)

    # Get image dimensions
    img_height, img_width = image.shape[:2]

    # Calculate bounding box coordinates
    x_min = int((x_center - x_len / 2) * img_width)
    x_max = int((x_center + x_len / 2) * img_width)
    y_min = int((y_center - y_height / 2) * img_height)
    y_max = int((y_center + y_height / 2) * img_height)

    # Overlay the bounding box on the image
    cv2.rectangle(image, (x_min, y_min), (x_max, y_max), (0, 255, 0), 2)

    # Save the new image in the output directory
    output_image_path = os.path.join(output_dir, corresponding_png_file)
    cv2.imwrite(output_image_path, image)

    print(f"Image with bounding box saved to {output_image_path}")


In [ ]:
labels_dir = 'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/labels'
images_dir = 'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/images'
output_dir = 'drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/testing_txt_png_pairs'
for i in range (0,8):
  overlay_bounding_box(labels_dir, images_dir, output_dir)

Image with bounding box saved to drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/testing_txt_png_pairs/Tyler STMN2a Touch Responses_2a KO 18_frame_065.png
Image with bounding box saved to drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/testing_txt_png_pairs/CRISPent inppf5 Touch Response 12-06-24_TR_inppf5_52hpf_19_frame_070.png
Image with bounding box saved to drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/testing_txt_png_pairs/Tyler Double KO Touch Responses_Double KO 23_frame_054.png
Image with bounding box saved to drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/testing_txt_png_pairs/Tyler STMN2b Touch Responses_2b KO 4_frame_046.png
Image with bounding box saved to drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/testing_txt_png_pairs/Tyler STMN2b Touch Responses_2b KO 24_frame_105.png
Image with bounding box saved to drive/MyDrive/Colab Notebooks/Zebrafish Frames and Annotations/testing_txt_png_pairs/Tyler